- augmenter la RAM utilisée par SPARK !! : http://www.datastax.com/dev/blog/zen-art-spark-maintenance, http://www.datastax.com/dev/blog/common-spark-troubleshooting : **plus ou moins fait... à ajuster éventuellement**
- faire la table dans cassandra **fait : vérifier que le schéma est correct**
- dropper le poids ** oublié... à faire : changer le schéma de la table dans cqlsh et changer le code de chargement des DataFrame**
- ajouter une colonne date (full timestamp) ** fait **
- insérer fichier par fichier ? charger par batch de fichiers ? ** en test **
- possible de paralleliser ? ** je ne pense pas : idée ? **
- faire un test sur la vitesse de chargement : ** en cours **

----

## Vérification du bon fonctionnement de PySpark

In [1]:
print(sc)

In [2]:
sc.master

u'spark://172.31.20.22:7077'

In [4]:
rdd = sc.parallelize([1, 2, 3], 2).map(lambda x: x*2).filter(lambda x: x > 2).collect()

In [3]:
rdd = sc.parallelize(xrange(10000000), 8)

In [4]:
rdd.getNumPartitions()

8

In [5]:
rdd.cache()

PythonRDD[1] at RDD at PythonRDD.scala:43

In [7]:
rdd.map(lambda x: (x % 1000, x)).filter(lambda x : x[0] % 5 == 0).groupByKey().mapValues(list).collect()

[(0,
  [0,
   1000,
   2000,
   3000,
   4000,
   5000,
   6000,
   7000,
   8000,
   9000,
   10000,
   11000,
   12000,
   13000,
   14000,
   15000,
   16000,
   17000,
   18000,
   19000,
   20000,
   21000,
   22000,
   23000,
   24000,
   25000,
   26000,
   27000,
   28000,
   29000,
   30000,
   31000,
   32000,
   33000,
   34000,
   35000,
   36000,
   37000,
   38000,
   39000,
   40000,
   41000,
   42000,
   43000,
   44000,
   45000,
   46000,
   47000,
   48000,
   49000,
   50000,
   51000,
   52000,
   53000,
   54000,
   55000,
   56000,
   57000,
   58000,
   59000,
   60000,
   61000,
   62000,
   63000,
   64000,
   65000,
   66000,
   67000,
   68000,
   69000,
   70000,
   71000,
   72000,
   73000,
   74000,
   75000,
   76000,
   77000,
   78000,
   79000,
   80000,
   81000,
   82000,
   83000,
   84000,
   85000,
   86000,
   87000,
   88000,
   89000,
   90000,
   91000,
   92000,
   93000,
   94000,
   95000,
   96000,
   97000,
   98000,
   99000,
   10000

In [4]:
rdd

[4, 6]

---

## Chargement des données

In [5]:
from os import listdir
from os.path import isfile, join
import re
from time import time
from pyspark.sql import SQLContext
sql = SQLContext(sc)

On récupère la liste des fichiers

In [6]:
directory = '/mnt/wikidata/wikistats/'
datafiles = [f for f in listdir(directory) 
             if isfile(join(directory, f)) and f.startswith('pagecounts')]
print('Il existe {} fichiers.'.format(len(datafiles)))

Il existe 2160 fichiers.


A chaque fichier on associer un datastamp :

In [7]:
def extract_date(datafile):
    rex = re.compile(r'pagecounts-(\d{4})(\d{2})(\d{2})-(\d{2}).*')
    s = rex.match(datafile)
    datetime = '{}-{}-{} {}:00'.format(*(s.group(i) for i in range(1, 5)))
    return datetime

In [8]:
datafiles_datetimes = [(datafile, extract_date(datafile)) for datafile in datafiles]

In [9]:
datafiles_datetimes[:10]

[('pagecounts-20110130-070000.gz', '2011-01-30 07:00'),
 ('pagecounts-20110305-210000.gz', '2011-03-05 21:00'),
 ('pagecounts-20110113-180000.gz', '2011-01-13 18:00'),
 ('pagecounts-20110313-220000.gz', '2011-03-13 22:00'),
 ('pagecounts-20110101-060000.gz', '2011-01-01 06:00'),
 ('pagecounts-20110314-110000.gz', '2011-03-14 11:00'),
 ('pagecounts-20110124-110000.gz', '2011-01-24 11:00'),
 ('pagecounts-20110116-220000.gz', '2011-01-16 22:00'),
 ('pagecounts-20110108-230000.gz', '2011-01-08 23:00'),
 ('pagecounts-20110109-060000.gz', '2011-01-09 06:00')]

In [10]:
def create_row(row, datetime):
    projectcode, page, views, _ = row.split(' ')
    return [datetime, projectcode, page, int(views)]

In [11]:
def no_points(row):
    return '.' not in row[1]

On teste le premier fichier.

In [12]:
datafile = datafiles_datetimes[7][0]
datetime = datafiles_datetimes[7][1]
path='file:///mnt/wikidata/wikistats/' + datafile 

In [13]:
rdd0 = sc.textFile(path, minPartitions=5).map(lambda r: create_row(r, datetime)).filter(no_points)

In [28]:
rdd0.repartition(2)

MapPartitionsRDD[11] at repartition at NativeMethodAccessorImpl.java:-2

In [14]:
rdd0.getNumPartitions()

1

In [15]:
rdd0.count()

5711605

In [134]:
datafile = datafiles_datetimes[8][0]
datetime = datafiles_datetimes[8][1]
path='file:///mnt/wikidata/wikistats/' + datafile 

In [135]:
rdd = sc.textFile(path, minPartitions=5).map(lambda r: create_row(r, datetime)).filter(no_points)

In [136]:
rdd0 = rdd0.union(rdd)

In [137]:
rdd0.getNumPartitions()

2

In [138]:
rdd0.repartition(5)

MapPartitionsRDD[290] at repartition at NativeMethodAccessorImpl.java:-2

In [ ]:
df = sql.createDataFrame(rdd, schema=['datetime', 'projectcode', 'page', 'views'])

In [91]:
t0 = time()
df.write.format("org.apache.spark.sql.cassandra").\
        options(table="wikidata", keyspace="projet").\
        save(mode="append")
t1 = time()

In [93]:
(t1 - t0) // 60, (t1 - t0) % 60

(4.0, 34.01799392700195)

In [50]:
df.write.format("org.apache.spark.sql.cassandra").\
    options(table="wikipediadata", keyspace="projet").\
    save(mode="append")

On time l'insertion de 10 fichiers via le master:

In [52]:
ts = [time()]
for datafile, datetime in datafiles_datetimes[1:11]:
    rdd = sc.textFile(path).map(lambda r: [datetime] + r.split(' '))
    df = sql.createDataFrame(rdd, schema=['datetime', 'projectcode', 'page', 'views', 'weight'])
    df.write.format("org.apache.spark.sql.cassandra").\
        options(table="wikipediadata", keyspace="projet").\
        save(mode="append")
    ts.append(time())

In [55]:
with open("log_time", "a") as f:
    for i, t in enumerate(ts[1:]):
        f.write('Chargement du fichier {} : {} secondes.\n'.format(i, t-ts[i]))
    total = ts[-1] - ts[0]
    m = total // 60
    s = total % 60
    f.write('Temps total pour 10 fichiers : {} minutes {} secondes\n'.format(m, s))

On time l'insertion de 3 fichiers via le master, avec concatenation de ces fichiers avant l'écriture dans Cassandra.

In [97]:
ts = [time()]
global_rdd = None
for datafile, datetime in datafiles_datetimes[4:7]:
    rdd = sc.textFile(path).map(lambda r: create_row(r, datetime)).filter(no_points)
    if global_rdd is None:
        global_rdd = rdd
    else:
        global_rdd.union(rdd)
    ts.append(time())
df = sql.createDataFrame(global_rdd, schema=['datetime', 'projectcode', 'page', 'views', 'weight'])
df.write.format("org.apache.spark.sql.cassandra").\
    options(table="wikipediadata", keyspace="projet").\
    save(mode="append")
ts.append(time())

In [98]:
with open("log_time", "a") as f:
    for i, t in enumerate(ts[1:]):
        f.write('Chargement du fichier {} : {} secondes.\n'.format(i, t-ts[i]))
    f.write('Ecriture de la dataframe de 3 fichiers {} : {} secondes.\n'.format(i, ts[-1]-ts[-2]))
    total = ts[-1] - ts[0]
    m = total // 60
    s = total % 60
    f.write('Temps total pour 3 fichiers : {} minutes {} secondes\n'.format(m, s))

---

In [5]:
user = sql.read.format("org.apache.spark.sql.cassandra").\
               load(keyspace="training", table="user")

In [6]:
adults = user.where(user.age > 21)


In [7]:
adults.show()


+-------+---+--------------------+-------+
|user_id|age|      favorite_foods|   name|
+-------+---+--------------------+-------+
|      3|108|ArrayBuffer(Muffi...|Patrick|
|      1| 34|ArrayBuffer(Bacon...|    Jon|
|      2| 22|ArrayBuffer(Kale,...|   Dani|
+-------+---+--------------------+-------+

